In [17]:
# Cell 1
import os
import joblib
import numpy as np
import pandas as pd
import mlflow
import optuna
from optuna.integration import MLflowCallback
from sklearn.model_selection import cross_val_predict, StratifiedKFold
from sklearn.preprocessing import LabelEncoder

import xgboost as xgb
from sklearn.ensemble import RandomForestClassifier, ExtraTreesClassifier

import sys
import os
sys.path.append(os.path.abspath(".."))
from src.metrics import multiclass_and_binary_metrics
from src.utils import save_json, load_json, save_df

mlflow.set_experiment("iml2025_project")

os.makedirs("../models", exist_ok=True)
os.makedirs("../logs/metrics", exist_ok=True)


In [19]:
# Cell 2
train = pd.read_csv("../data/train_fe.csv")
train["class2"] = (train["class4"] != "nonevent").astype(int)

# features and labels (string)
X = train.drop(columns=["class4", "class2"])
y_class4 = train["class4"].values            # strings like 'II','Ia','Ib','nonevent'
y_binary = train["class2"].values

# load class_list (alphabetical per Option A) created earlier in Notebook2
class_list = load_json("../models/class_list.json")
print("class_list (loaded):", class_list)

# Label encode using the class_list order (ensures stable mapping)
le = LabelEncoder()
le.fit(class_list)                 # IMPORTANT: fit on saved class_list to fix mapping
y_class4_int = le.transform(y_class4)  # integer labels 0..K-1

# check mapping
mapping = {lab:int(idx) for idx,lab in enumerate(le.classes_)}
print("LabelEncoder mapping (label -> int):", mapping)

cv = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)
alpha = 0.7   # composite loss weight (0..1) - weight for binary_logloss


class_list (loaded): ['II', 'Ia', 'Ib', 'nonevent']
LabelEncoder mapping (label -> int): {np.str_('II'): 0, np.str_('Ia'): 1, np.str_('Ib'): 2, np.str_('nonevent'): 3}


In [20]:
# Cell 3
def composite_oof_loss(y_class4_strings, oof_probs, nonevent_label="nonevent"):
    """
    Returns (metrics_dict, composite_loss) given:
    - y_class4_strings: original string labels (len=n)
    - oof_probs: ndarray (n, k) ordered by integer class indices (0..k-1) matching class_list
    """
    metrics = multiclass_and_binary_metrics(y_class4_strings, oof_probs, nonevent_label=nonevent_label, class_list=class_list)
    loss = alpha * metrics["binary_logloss"] + (1 - alpha) * metrics["multiclass_logloss"]
    return metrics, loss


# ExtraTrees Optuna Tuning

In [21]:
# Cell 4
def objective_extratrees(trial):
    params = {
        "n_estimators": trial.suggest_int("n_estimators", 300, 1200),
        "max_depth": trial.suggest_int("max_depth", 4, 20),
        "min_samples_split": trial.suggest_int("min_samples_split", 2, 20),
        "min_samples_leaf": trial.suggest_int("min_samples_leaf", 1, 10),
        "max_features": trial.suggest_categorical("max_features", ["sqrt", "log2", None]),
        "bootstrap": False,
        "n_jobs": -1,
        "random_state": 42
    }
    model = ExtraTreesClassifier(**params)
    # Use integer labels for CV fitting
    oof = cross_val_predict(model, X, y_class4_int, cv=cv, method="predict_proba", n_jobs=-1)
    metrics, loss = composite_oof_loss(y_class4, oof)
    trial.set_user_attr("metrics", metrics)
    return loss


In [22]:
# Cell 5
study_et = optuna.create_study(direction="minimize", study_name="extratrees_tuning")
mlflow_cb = MLflowCallback(tracking_uri=mlflow.get_tracking_uri(), metric_name="composite_loss")
study_et.optimize(objective_extratrees, n_trials=150, callbacks=[mlflow_cb])

best_et_params = study_et.best_params
print("Best ExtraTrees params:", best_et_params)
save_json(best_et_params, "../models/optuna_best_et_params.json")


[I 2025-12-07 11:50:33,893] A new study created in memory with name: extratrees_tuning
/tmp/ipykernel_408552/2904310847.py:3: ExperimentalWarning: MLflowCallback is experimental (supported from v1.4.0). The interface can change in the future.
  mlflow_cb = MLflowCallback(tracking_uri=mlflow.get_tracking_uri(), metric_name="composite_loss")
Traceback (most recent call last):
  File "/home/ayesh/miniforge3/envs/npf-classifier/lib/python3.14/site-packages/joblib/externals/loky/backend/resource_tracker.py", line 297, in main
    raise ValueError(
    ...<4 lines>...
    )
ValueError: Cannot register "REGISTER","rtype":"folder","base64_name" for automatic cleanup: unknown resource type ("L2Rldi9zaG0vam9ibGliX21lbW1hcHBpbmdfZm9sZGVyXzQwODU1Ml8yN2QyZjczNTQ3NmE0MzIzODI4ZjU2YWFmNzQxY2QyYV80NjQyMTJiMGQ0ODY0YTVkYTA4OWZkNTY4NmU4NjI2Yw=="}). Resource type should be one of the following: ['noop', 'folder', 'file', 'semlock']
Traceback (most recent call last):
  File "/home/ayesh/miniforge3/envs/npf-

Best ExtraTrees params: {'n_estimators': 634, 'max_depth': 16, 'min_samples_split': 3, 'min_samples_leaf': 3, 'max_features': 'sqrt'}


In [23]:
# Cell 6
best_et = ExtraTreesClassifier(**best_et_params, n_jobs=-1, random_state=42)
best_et.fit(X, y_class4_int)
joblib.dump(best_et, "../models/best_extratrees_full.joblib")

# recompute OOF (fitted estimator with CV)
oof_et = cross_val_predict(best_et, X, y_class4_int, cv=cv, method="predict_proba", n_jobs=-1)
np.save("../models/oof_best_et_multiclass.npy", oof_et)

metrics_et, loss_et = composite_oof_loss(y_class4, oof_et)
print("ExtraTrees tuned OOF metrics:", metrics_et)


Traceback (most recent call last):
  File "/home/ayesh/miniforge3/envs/npf-classifier/lib/python3.14/site-packages/joblib/externals/loky/backend/resource_tracker.py", line 297, in main
    raise ValueError(
    ...<4 lines>...
    )
ValueError: Cannot register "REGISTER","rtype":"folder","base64_name" for automatic cleanup: unknown resource type ("L2Rldi9zaG0vam9ibGliX21lbW1hcHBpbmdfZm9sZGVyXzQwODU1Ml82ZWI5OGI5MDhhYTI0NjMxOTBhOGYyYWFlOTU3YTY2N183MTBhMmM3ZDQzNDg0YjFlYmNhODVhMDY5ZTY1NmQ0ZA=="}). Resource type should be one of the following: ['noop', 'folder', 'file', 'semlock']
Traceback (most recent call last):
  File "/home/ayesh/miniforge3/envs/npf-classifier/lib/python3.14/site-packages/joblib/externals/loky/backend/resource_tracker.py", line 297, in main
    raise ValueError(
    ...<4 lines>...
    )
ValueError: Cannot register "REGISTER","rtype":"folder","base64_name" for automatic cleanup: unknown resource type ("L2Rldi9zaG0vam9ibGliX21lbW1hcHBpbmdfZm9sZGVyXzQwODU1Ml9iNDgxYmZmMTl

ExtraTrees tuned OOF metrics: {'multiclass_logloss': 0.7749648102320494, 'class4_accuracy': 0.66, 'binary_logloss': 0.33811032405357294, 'class2_accuracy': 0.8666666666666667, 'perplexity': 1.402295201762653}


Traceback (most recent call last):
  File "/home/ayesh/miniforge3/envs/npf-classifier/lib/python3.14/site-packages/joblib/externals/loky/backend/resource_tracker.py", line 297, in main
    raise ValueError(
    ...<4 lines>...
    )
ValueError: Cannot register "UNREGISTER","rtype":"semlock","base64_name" for automatic cleanup: unknown resource type ("L2xva3ktNDU3MTE1LV81cV9uZW9o"}). Resource type should be one of the following: ['noop', 'folder', 'file', 'semlock']
Traceback (most recent call last):
  File "/home/ayesh/miniforge3/envs/npf-classifier/lib/python3.14/site-packages/joblib/externals/loky/backend/resource_tracker.py", line 297, in main
    raise ValueError(
    ...<4 lines>...
    )
ValueError: Cannot register "UNREGISTER","rtype":"semlock","base64_name" for automatic cleanup: unknown resource type ("L2xva3ktNDU3MTE1LXZ6NmFlN2ho"}). Resource type should be one of the following: ['noop', 'folder', 'file', 'semlock']
Traceback (most recent call last):
  File "/home/ayesh/minif

# XGBoost Optuna Tuning

In [24]:
# Cell 7
def objective_xgb(trial):
    params = {
        "objective": "multi:softprob",
        "num_class": len(class_list),
        "eval_metric": "mlogloss",
        "tree_method": "hist",

        "n_estimators": trial.suggest_int("n_estimators", 200, 900),
        "max_depth": trial.suggest_int("max_depth", 2, 10),
        "learning_rate": trial.suggest_float("learning_rate", 0.01, 0.3),
        "subsample": trial.suggest_float("subsample", 0.6, 1.0),
        "colsample_bytree": trial.suggest_float("colsample_bytree", 0.6, 1.0),

        # Regularization
        "reg_alpha": trial.suggest_float("reg_alpha", 0.0, 2.0),
        "reg_lambda": trial.suggest_float("reg_lambda", 0.5, 3.0),
        "min_child_weight": trial.suggest_int("min_child_weight", 1, 20),

        "random_state": 42
    }
    model = xgb.XGBClassifier(**params)
    oof = cross_val_predict(model, X, y_class4_int, cv=cv, method="predict_proba")
    metrics, loss = composite_oof_loss(y_class4, oof)
    trial.set_user_attr("metrics", metrics)
    return loss


In [25]:
# Cell 8
study_xgb = optuna.create_study(direction="minimize", study_name="xgb_tuning")
study_xgb.optimize(objective_xgb, n_trials=150, callbacks=[mlflow_cb])

best_xgb_params = study_xgb.best_params
print("Best XGB params:", best_xgb_params)
save_json(best_xgb_params, "../models/optuna_best_xgb_params.json")


[I 2025-12-07 11:59:22,592] A new study created in memory with name: xgb_tuning
[I 2025-12-07 11:59:33,286] Trial 0 finished with value: 0.4987310052482724 and parameters: {'n_estimators': 222, 'max_depth': 8, 'learning_rate': 0.1569630848064698, 'subsample': 0.6984222863774399, 'colsample_bytree': 0.8396312283825829, 'reg_alpha': 1.3356221068236618, 'reg_lambda': 2.580941569194525, 'min_child_weight': 8}. Best is trial 0 with value: 0.4987310052482724.
[I 2025-12-07 11:59:46,446] Trial 1 finished with value: 0.534872699020816 and parameters: {'n_estimators': 496, 'max_depth': 10, 'learning_rate': 0.22147350544482472, 'subsample': 0.6015978535268555, 'colsample_bytree': 0.7798332052664524, 'reg_alpha': 1.102170889632972, 'reg_lambda': 2.9409793592380917, 'min_child_weight': 11}. Best is trial 0 with value: 0.4987310052482724.
[I 2025-12-07 11:59:58,409] Trial 2 finished with value: 0.5810641206780491 and parameters: {'n_estimators': 646, 'max_depth': 2, 'learning_rate': 0.2866151559922

Best XGB params: {'n_estimators': 240, 'max_depth': 3, 'learning_rate': 0.03443565753469065, 'subsample': 0.6751469063927528, 'colsample_bytree': 0.7130626523368424, 'reg_alpha': 0.06430727056746484, 'reg_lambda': 2.7287324022320107, 'min_child_weight': 3}


In [26]:
# Cell 9
best_xgb = xgb.XGBClassifier(**best_xgb_params)
best_xgb.fit(X, y_class4_int)
joblib.dump(best_xgb, "../models/best_xgb_full.joblib")

oof_xgb = cross_val_predict(best_xgb, X, y_class4_int, cv=cv, method="predict_proba")
np.save("../models/oof_best_xgb_multiclass.npy", oof_xgb)

metrics_xgb, loss_xgb = composite_oof_loss(y_class4, oof_xgb)
print("XGB tuned OOF metrics:", metrics_xgb)


XGB tuned OOF metrics: {'multiclass_logloss': 0.7853929648803682, 'class4_accuracy': 0.6844444444444444, 'binary_logloss': 0.319341736698166, 'class2_accuracy': 0.8666666666666667, 'perplexity': 1.3762215499633133}


# Random Forest Optuna Tuning

In [27]:
# Cell 10
def objective_rf(trial):
    params = {
        "n_estimators": trial.suggest_int("n_estimators", 200, 1200),
        "max_depth": trial.suggest_int("max_depth", 4, 30),
        "min_samples_split": trial.suggest_int("min_samples_split", 2, 30),
        "min_samples_leaf": trial.suggest_int("min_samples_leaf", 1, 15),
        "max_features": trial.suggest_categorical("max_features", ["sqrt", "log2", None]),
        "bootstrap": trial.suggest_categorical("bootstrap", [True, False]),
        "n_jobs": -1,
        "random_state": 42
    }
    model = RandomForestClassifier(**params)
    oof = cross_val_predict(model, X, y_class4_int, cv=cv, method="predict_proba", n_jobs=-1)
    metrics, loss = composite_oof_loss(y_class4, oof)
    trial.set_user_attr("metrics", metrics)
    return loss


In [28]:
# Cell 11
study_rf = optuna.create_study(direction="minimize", study_name="rf_tuning")
study_rf.optimize(objective_rf, n_trials=150, callbacks=[mlflow_cb])

best_rf_params = study_rf.best_params
print("Best RF params:", best_rf_params)
save_json(best_rf_params, "../models/optuna_best_rf_params.json")


[I 2025-12-07 12:35:54,439] A new study created in memory with name: rf_tuning
Traceback (most recent call last):
  File "/home/ayesh/miniforge3/envs/npf-classifier/lib/python3.14/site-packages/joblib/externals/loky/backend/resource_tracker.py", line 297, in main
    raise ValueError(
    ...<4 lines>...
    )
ValueError: Cannot register "REGISTER","rtype":"folder","base64_name" for automatic cleanup: unknown resource type ("L2Rldi9zaG0vam9ibGliX21lbW1hcHBpbmdfZm9sZGVyXzQwODU1Ml81ODQ3OWU1Mzc2MTk0MDYxOWQxNTUxODY4ZjEzOGQ5Nl9kODNhZWY4M2ZmMDU0ZmE4ODI3YjlmMzc4ODVkMGMzYw=="}). Resource type should be one of the following: ['noop', 'folder', 'file', 'semlock']
Traceback (most recent call last):
  File "/home/ayesh/miniforge3/envs/npf-classifier/lib/python3.14/site-packages/joblib/externals/loky/backend/resource_tracker.py", line 297, in main
    raise ValueError(
    ...<4 lines>...
    )
ValueError: Cannot register "REGISTER","rtype":"folder","base64_name" for automatic cleanup: unknown reso

Best RF params: {'n_estimators': 930, 'max_depth': 17, 'min_samples_split': 14, 'min_samples_leaf': 12, 'max_features': 'sqrt', 'bootstrap': False}


In [29]:
# Cell 12
best_rf = RandomForestClassifier(**best_rf_params)
best_rf.fit(X, y_class4_int)
joblib.dump(best_rf, "../models/best_rf_full.joblib")

oof_rf = cross_val_predict(best_rf, X, y_class4_int, cv=cv, method="predict_proba", n_jobs=-1)
np.save("../models/oof_best_rf_multiclass.npy", oof_rf)

metrics_rf, loss_rf = composite_oof_loss(y_class4, oof_rf)
print("RF tuned OOF metrics:", metrics_rf)


Traceback (most recent call last):
  File "/home/ayesh/miniforge3/envs/npf-classifier/lib/python3.14/site-packages/joblib/externals/loky/backend/resource_tracker.py", line 297, in main
    raise ValueError(
    ...<4 lines>...
    )
ValueError: Cannot register "REGISTER","rtype":"folder","base64_name" for automatic cleanup: unknown resource type ("L2Rldi9zaG0vam9ibGliX21lbW1hcHBpbmdfZm9sZGVyXzQwODU1Ml84OTBlOWQwMDAwNTc0ODlmOGFjYmQwODcyYjBkNDYyZV8xNTMzY2EyZjU2MDk0ZjAyODY0ZTc3MWQ4MjExZjkwMQ=="}). Resource type should be one of the following: ['noop', 'folder', 'file', 'semlock']
Traceback (most recent call last):
  File "/home/ayesh/miniforge3/envs/npf-classifier/lib/python3.14/site-packages/joblib/externals/loky/backend/resource_tracker.py", line 297, in main
    raise ValueError(
    ...<4 lines>...
    )
ValueError: Cannot register "REGISTER","rtype":"folder","base64_name" for automatic cleanup: unknown resource type ("L2Rldi9zaG0vam9ibGliX21lbW1hcHBpbmdfZm9sZGVyXzQwODU1Ml9iNDgxYmZmMTl

RF tuned OOF metrics: {'multiclass_logloss': 0.7802197015501051, 'class4_accuracy': 0.6333333333333333, 'binary_logloss': 0.34424362588574486, 'class2_accuracy': 0.86, 'perplexity': 1.410922330842007}


Traceback (most recent call last):
  File "/home/ayesh/miniforge3/envs/npf-classifier/lib/python3.14/site-packages/joblib/externals/loky/backend/resource_tracker.py", line 297, in main
    raise ValueError(
    ...<4 lines>...
    )
ValueError: Cannot register "UNREGISTER","rtype":"folder","base64_name" for automatic cleanup: unknown resource type ("L2Rldi9zaG0vam9ibGliX21lbW1hcHBpbmdfZm9sZGVyXzQwODU1Ml9iNDgxYmZmMTlmOTI0YzEzYjI1ODJmYWY5ZDgwMDAxYl8wOGY2MTlhODg3NjI0NGRmOWIyMThmNjg1ZDFmYTQwMg=="}). Resource type should be one of the following: ['noop', 'folder', 'file', 'semlock']


# Summary

In [31]:
# Cell 13
summary = {
    "extratrees": metrics_et if "metrics_et" in globals() else {},
    "xgb": metrics_xgb if "metrics_xgb" in globals() else {},
    "randomforest": metrics_rf if "metrics_rf" in globals() else {}
}
save_json(summary, "../models/tuned_models_oof_metrics_summary.json")
summary


{'extratrees': {'multiclass_logloss': 0.7749648102320494,
  'class4_accuracy': 0.66,
  'binary_logloss': 0.33811032405357294,
  'class2_accuracy': 0.8666666666666667,
  'perplexity': 1.402295201762653},
 'xgb': {'multiclass_logloss': 0.7853929648803682,
  'class4_accuracy': 0.6844444444444444,
  'binary_logloss': 0.319341736698166,
  'class2_accuracy': 0.8666666666666667,
  'perplexity': 1.3762215499633133},
 'randomforest': {'multiclass_logloss': 0.7802197015501051,
  'class4_accuracy': 0.6333333333333333,
  'binary_logloss': 0.34424362588574486,
  'class2_accuracy': 0.86,
  'perplexity': 1.410922330842007}}

Traceback (most recent call last):
  File "/home/ayesh/miniforge3/envs/npf-classifier/lib/python3.14/site-packages/joblib/externals/loky/backend/resource_tracker.py", line 297, in main
    raise ValueError(
    ...<4 lines>...
    )
ValueError: Cannot register "UNREGISTER","rtype":"semlock","base64_name" for automatic cleanup: unknown resource type ("L2xva3ktNDA4NTUyLTQzX3hpbDlk"}). Resource type should be one of the following: ['noop', 'folder', 'file', 'semlock']
Traceback (most recent call last):
  File "/home/ayesh/miniforge3/envs/npf-classifier/lib/python3.14/site-packages/joblib/externals/loky/backend/resource_tracker.py", line 297, in main
    raise ValueError(
    ...<4 lines>...
    )
ValueError: Cannot register "UNREGISTER","rtype":"semlock","base64_name" for automatic cleanup: unknown resource type ("L2xva3ktNDA4NTUyLXF4NDVhOGlt"}). Resource type should be one of the following: ['noop', 'folder', 'file', 'semlock']
Traceback (most recent call last):
  File "/home/ayesh/minif

In [30]:
from src.utils import save_df

rows = []
rows.append({"model":"ExtraTrees", **metrics_et})
rows.append({"model":"XGBoost", **metrics_xgb})
rows.append({"model":"RandomForest", **metrics_rf})
df_summary = pd.DataFrame(rows)
save_df(df_summary, "../logs/metrics/tuned_models_oof_metrics_summary.csv")
df_summary

model  multiclass_logloss  class4_accuracy  binary_logloss  \
0    ExtraTrees            0.774965         0.660000        0.338110   
1       XGBoost            0.785393         0.684444        0.319342   
2  RandomForest            0.780220         0.633333        0.344244   

   class2_accuracy  perplexity  
0         0.866667    1.402295  
1         0.866667    1.376222  
2         0.860000    1.410922